# Finding frequent itemsets with the Apriori algorithm

This Jupyter notebook is based on the following publication:
    
    Harrington, P. Machine Learning in Action. 
        Association analysis with the Apriori algorithm (Chapter 11).
    Manning Publications Co., 2012

### Apriori algorithm

The way to find frequent itemsets is the **Apriori algorithm**. The Apriori algorithm
needs a **minimum support level** as an input and a data set. The algorithm will generate
a list of all **candidate itemsets** with one item. The transaction data set will then be
scanned to see which sets meet the minimum support level. Sets that don't meet the
minimum support level will get tossed out.

The remaining sets will then be combined
to make itemsets with two elements. Again, the transaction dataset will be scanned
and itemsets not meeting the minimum support level will get tossed. This procedure
will be repeated until all sets are tossed out.

### Data

The following function creates a simple data set.

In [1]:
def Load_data():
    baskets_data = [
        ['kruh', 'mleko'],
        ['kruh', 'plenice', 'union'],
        ['mleko', 'plenice', 'union'],
        ['kruh', 'mleko', 'plenice', 'union'],
        ['kruh', 'mleko', 'plenice'],
        ['mleko', 'plenice'],
        ['plenice'],
        ['mleko', 'union', 'plenice'],
        ['plenice', 'union'],
        ['mleko', 'plenice', 'union'],
    ]
    return baskets_data

### Generating candidate itemsets

Pseudocode for scanning the dataset would look like this:
    
    For each transaction tran in the dataset:
        For each candidate itemset, can:
            Check to see if can is a subset of tran
            If so increment the count of can
    
    For each candidate itemset:
        If the support meets the minimum, keep this item
    
    Return list of frequent itemsets

The following function creates C1: a candidate itemset of size one. In the Apriori algorithm, we create C1, and then we'll scan the dataset to see if these one itemsets meet our minimum support requirements.

We need a special function for the first list of candidate itemsets because
initially you're reading from input, whereas later lists will be properly formatted.

In [2]:
def createC1(data):
    """
    Create a list of unique items in transaction data.
    Represent each item as a set of length 1.
    """
    C1 = []
    for transaction in data:
        for item in transaction:
            if not [item] in C1:
                C1.append([item])
    C1.sort()
    
    # create a set for each item in C1
    return [set(x) for x in C1]

The function createCk() will take a list of frequent itemsets, Lk, and the size of
the itemsets, k, to produce Ck. This is accomplished by first creating an empty
list and then measuring how many elements are in Lk.

Next, compare each item in Lk with all of the other items in Lk. The two `for` loops accomplish that. 

Next, take two sets in our list and compare them. If **the first `k-2` items** are equal, then combine
the two sets to make a set of size k. B The sets are combined using the set union,
which is the | symbol in Python.

In [3]:
def createCk(Lk, k):
    """
    Create a list of candidates of length k.
    
    Arguments:
       Lk: a list of frequent itemsets
       k: the size of the itemsets
    
    """
    cand_list = []
    len_Lk = len(Lk)
    
    # join sets if first k-2 items are equal
    for i in range(len_Lk):
        for j in range(i+1, len_Lk):
            L1 = list(Lk[i])[:k-2]
            L2 = list(Lk[j])[:k-2]
            L1.sort()
            L2.sort()
            if L1==L2:
                cand_list.append(Lk[i] | Lk[j])
    
    return cand_list

The following function is used to generate a **list of itemsets** from candidate sets. It also returns a dictionary with **support values** for use later.

This function creates an empty dictionary, `count`, and then goes over all the transactions in
the dataset and all the candidate sets in `Ck`. If the sets of `Ck` are part of the dataset,
then increment the count in the dictionary. The set is the key in the dictionary.

After scanning over all the items in the dataset and all the candidate sets, we
need to calculate the support. Sets that don't meet your minimum support levels
won't be output. 

First, we create an empty list that will hold the sets that do meet the
minimum support. The next loop goes over every element in the dictionary and measures
the support.

In [4]:
def scanD(data, Ck, min_support):
    """
    Scan through transaction data and return a list of candidates that meet
    the support threshold, and support data about the current candidates.
    
    Arguments:
       data: data set,
       Ck: a list of candidate sets
       min_support: the minimum support
    """
    count = {}
    for transaction in data:
        tr = set(transaction)
        for candidate in Ck:
            if candidate.issubset(tr):
                can = frozenset(candidate)
                if can not in count:
                    count[can] = 1
                else:
                    count[can] += 1
                    num_items = float(len(D))
    
    cand_list = []
    support_data = {}
    
    # calculate support for every itemset
    for key in count:
        support = count[key]/num_items
        
        # If the support meets the minimum support requirements, 
        # add it to the list of itemsets.
        if support >= min_support:
            cand_list.insert(0, key)
        support_data[key] = support
    
    return cand_list, support_data

### Run Apriori

Pseudo-code for the whole Apriori algorithm would look like this:

    While the number of items in the set is greater than 0:
        Create a list of candidate itemsets of length k
        Scan the dataset to see if each itemset is frequent
        Keep frequent itemsets to create itemsets of length k+1

In [5]:
min_support = 0.5

In [6]:
data = Load_data()
data

[['kruh', 'mleko'],
 ['kruh', 'plenice', 'union'],
 ['mleko', 'plenice', 'union'],
 ['kruh', 'mleko', 'plenice', 'union'],
 ['kruh', 'mleko', 'plenice'],
 ['mleko', 'plenice'],
 ['plenice'],
 ['mleko', 'union', 'plenice'],
 ['plenice', 'union'],
 ['mleko', 'plenice', 'union']]

#### k = 1

In [7]:
C1 = createC1(data)
C1

[{'kruh'}, {'mleko'}, {'plenice'}, {'union'}]

In [8]:
D = list(map(set, data))
D

[{'kruh', 'mleko'},
 {'kruh', 'plenice', 'union'},
 {'mleko', 'plenice', 'union'},
 {'kruh', 'mleko', 'plenice', 'union'},
 {'kruh', 'mleko', 'plenice'},
 {'mleko', 'plenice'},
 {'plenice'},
 {'mleko', 'plenice', 'union'},
 {'plenice', 'union'},
 {'mleko', 'plenice', 'union'}]

In [9]:
L1, support_data1 = scanD(D, C1, min_support)

In [10]:
L1

[frozenset({'union'}), frozenset({'plenice'}), frozenset({'mleko'})]

In [11]:
support_data1

{frozenset({'kruh'}): 0.4,
 frozenset({'mleko'}): 0.7,
 frozenset({'plenice'}): 0.9,
 frozenset({'union'}): 0.6}

#### k = 2

In [12]:
C2 = createCk(L1, k=2)
C2

[frozenset({'plenice', 'union'}),
 frozenset({'mleko', 'union'}),
 frozenset({'mleko', 'plenice'})]

In [13]:
L2, support_data2 = scanD(D, C2, min_support)

In [14]:
L2

[frozenset({'mleko', 'plenice'}), frozenset({'plenice', 'union'})]

In [15]:
support_data2

{frozenset({'plenice', 'union'}): 0.6,
 frozenset({'mleko', 'union'}): 0.4,
 frozenset({'mleko', 'plenice'}): 0.6}

#### k = 3

In [16]:
C3 = createCk(L2, k=3)
C3

[frozenset({'mleko', 'plenice', 'union'})]

In [17]:
L3, support_data3 = scanD(D, C3, min_support)

In [18]:
L3

[]

In [19]:
support_data3

{frozenset({'mleko', 'plenice', 'union'}): 0.4}